In [1]:
import numpy as np
import pandas as pd
from IPython.display import HTML
from pandarallel import pandarallel
pandarallel.initialize()

pd.set_option('display.max_columns', 100)
pd.set_option('display.max_rows', 100)


INFO: Pandarallel will run on 8 workers.
INFO: Pandarallel will use standard multiprocessing data transfer (pipe) to transfer data between the main process and workers.


In [2]:
path_shared = '~/Downloads/nfl-big-data-bowl-2021/{}'

games_df = pd.read_csv(path_shared.format('games.csv'))
plays_df = pd.read_csv(path_shared.format('plays.csv'))
players_df = pd.read_csv(path_shared.format('players.csv'))
track_df = pd.read_csv(path_shared.format('week1_norm.csv'))

In [3]:
params = lambda: None # create an empty object to add params
params.a_max = 8
params.v_max = 9
params.reax_t = params.v_max/params.a_max
params.avg_ball_speed = 19.5
params.tti_sigma = 0.45
vars(params)

{'a_max': 8,
 'v_max': 9,
 'reax_t': 1.125,
 'avg_ball_speed': 19.5,
 'tti_sigma': 0.45}

In [4]:
# game_id = 2018122314
# play_id = 4239
game_id = 2018090905
play_id = 2062
# game_id, play_id = random.choice(plays)

play_df = track_df[(track_df.playId == play_id) & (track_df.gameId == game_id)].sort_values(by = 'frameId')
play_df.head()

gameId  playId  frameId event      nflId          displayName  \
317421  2018090905    2062        1  None   496735.0       Kareem Jackson   
317434  2018090905    2062        1  None        0.0             Football   
317433  2018090905    2062        1  None  2558094.0      Zach Cunningham   
317432  2018090905    2062        1  None  2552490.0  Benardrick McKinney   
317430  2018090905    2062        1  None  2552261.0        Kevin Johnson   

        jerseyNumber position      team team_pos teamAbbr route  \
317421          25.0       CB      away      DEF      HOU   NaN   
317434           NaN      NaN  football     FTBL     FTBL   NaN   
317433          41.0      ILB      away      DEF      HOU   NaN   
317432          55.0      ILB      away      DEF      HOU   NaN   
317430          30.0       CB      away      DEF      HOU   NaN   

                            time  los      x      y   dis       o     s  \
317421  2018-09-09T18:28:11.700Z   40  54.51  31.08  0.08  260.44  0.83   
317434  2018-09-09T18:28:11.700Z   40  40.18  29.52  0.00     NaN  0.00   
317433  2018-09-09T18:28:11.700Z   40  44.36  32.36  0.05  263.88  0.49   
317432  2018-09-09T18:28:11.700Z   40  41.88  23.53  0.10  220.61  0.95   
317430  2018-09-09T18:28:11.700Z   40  48.40  17.56  0.05  135.60  0.50   

         s_dir  s_dir_rad   v_x   v_y  v_theta  v_mag  a_old  a_x  a_y  \
317421  108.40       1.89  0.79 -0.26    -0.32   0.83   0.38  0.0  0.0   
317434     NaN        NaN  0.00  0.00     0.00   0.00   0.00  0.0  0.0   
317433  262.25       4.58 -0.49 -0.07     0.14   0.49   0.72  0.0  0.0   
317432  298.75       5.21 -0.83  0.46    -0.50   0.95   0.03  0.0  0.0   
317430   27.09       0.47  0.23  0.45     1.10   0.50   0.46  0.0  0.0   

        a_theta  a_mag  
317421      0.0    0.0  
317434      0.0    0.0  
317433      0.0    0.0  
317432      0.0    0.0  
317430      0.0    0.0

In [13]:
%%time
import time
from scipy.spatial import distance

def get_field_df(play_frame_group):
    frame_df = play_frame_group.loc[(play_df.nflId!=0)]
    ball_start = frame_df.loc[frame_df.position=='QB', ['x', 'y']].iloc[0].round(0)
    frame_df = frame_df.loc[frame_df.position!='QB']
    pocket_width = 10

    x = np.linspace(0.5, 119.5, 120)
    y = np.linspace(-0.5, 53.5, 55)
    
    t = np.linspace(0, 4, 41)

    receivers_df = frame_df.loc[(frame_df.team_pos == 'OFF') &
                                 ((frame_df.x > frame_df.los) |
                                  (frame_df.y > ball_start[1] + pocket_width // 2) |
                                  (frame_df.y < ball_start[1] - pocket_width // 2)),
                                 ['x', 'y', 'v_x', 'v_y', 'los']]
    # receivers_df['dist_from_ball'] = np.linalg.norm((receivers_df.x - ball_start[0],
    #                                                  receivers_df.y - ball_start[1]))
    # find the spot the qb would aim at, leading the receiver in their current dir by the ball time
    receivers_df['target_x'] = receivers_df.x+receivers_df.v_x*t+0.5*receivers_df.a_x*t**2  # (T,)
    receivers_df['target_y'] = receivers_df.y+receivers_df.v_y*t+0.5*receivers_df.a_y*t**2  # (T,)
    # receivers_df['target_x'] = receivers_df.x+receivers_df.v_x*receivers_df.dist_from_ball/params.avg_ball_speed
    # receivers_df['target_y'] = receivers_df.y+receivers_df.v_y*receivers_df.dist_from_ball/params.avg_ball_speed

    target_rec_locs = receivers_df[['target_x', 'target_y']].to_numpy()  # (R, 2)
    field_locs = np.stack(np.meshgrid(x, y)).reshape(2, -1).T  # (F, 2)

    # (F, R, 2) showing the vec diff btwn Fth spot on field and Rth rec target spot
    reach_vecs = field_locs[:,None,:] - target_rec_locs
    #reach_vecs[np.linalg.norm(reach_vecs) > 10] = 0
    Sigma = np.repeat(np.eye(2)[None], target_rec_locs.shape[0], axis=0) # (R, 2, 2) covariance matrices for receivers
    vx = receivers_df.v_x.to_numpy()
    vy = receivers_df.v_y.to_numpy()
    at2 = np.arctan2(vy, vx)
    
    # (F, R) vectorized calc of reach_vec.T @ Sigma.inv @ reach_vec
    gauss_top = np.einsum('...i,...ij,...j', reach_vecs, np.linalg.inv(Sigma), reach_vecs)
    gauss_bottom = 2*np.pi*np.sqrt(np.linalg.det(Sigma))  # (R,)  bivariate Gaussian normalizer
    # (F, R). (i, j) element is probability that spot i on field is thrown to given receiver j is targeted
    gauss_pdf = np.exp(-gauss_top/2) / gauss_bottom
    # assumption: each rec has uniform prob of being targeted. can use heuristic based on separation later
    target_prob = gauss_pdf.sum(axis=1) / gauss_pdf.sum()  # (F,)
    # 90%ile is a guess at this point. can tune it or use a heuristic of each rec getting a 50 sq yd window
    #cutoff = np.percentile(target_prob, 90)
    #target_prob[target_prob < cutoff] = 0
    target_prob_mesh = target_prob.reshape(len(y), len(x))
    field_df = pd.DataFrame({
        'ball_start_x': ball_start[0],
        'ball_start_y': ball_start[1],
        'ball_end_x': field_locs[:,0],
        'ball_end_y': field_locs[:,1],
        'cp_off': target_prob
    })
    return field_df

field_dfs = play_df.loc[play_df.frameId <= play_df.loc[play_df.event=='pass_forward'].frameId.iloc[0]].groupby(['gameId', 'playId', 'frameId']).parallel_apply(get_field_df)
field_dfs = field_dfs.reset_index(3, drop=True).reset_index()
field_dfs

CPU times: user 216 ms, sys: 158 ms, total: 374 ms
Wall time: 795 ms


gameId  playId  frameId  ball_start_x  ball_start_y  ball_end_x  \
0       2018090905    2062        1          35.0          30.0        35.5   
1       2018090905    2062        1          35.0          30.0        36.5   
2       2018090905    2062        1          35.0          30.0        37.5   
3       2018090905    2062        1          35.0          30.0        38.5   
4       2018090905    2062        1          35.0          30.0        39.5   
...            ...     ...      ...           ...           ...         ...   
215887  2018090905    2062       46          31.0          30.0       115.5   
215888  2018090905    2062       46          31.0          30.0       116.5   
215889  2018090905    2062       46          31.0          30.0       117.5   
215890  2018090905    2062       46          31.0          30.0       118.5   
215891  2018090905    2062       46          31.0          30.0       119.5   

        ball_end_y         cp_off  
0              0.5   4.011296e-87  
1              0.5   1.319333e-85  
2              0.5   1.596356e-84  
3              0.5   7.105762e-84  
4              0.5   1.163582e-83  
...            ...            ...  
215887        53.3  1.030488e-312  
215888        53.3   0.000000e+00  
215889        53.3   0.000000e+00  
215890        53.3   0.000000e+00  
215891        53.3   0.000000e+00  

[215892 rows x 8 columns]

In [14]:
field_dfs.loc[field_dfs.frameId == 17].sort_values('cp_off', ascending=False)

gameId  playId  frameId  ball_start_x  ball_start_y  ball_end_x  \
76676  2018090905    2062       17          35.0          30.0        41.5   
74976  2018090905    2062       17          35.0          30.0        41.5   
75145  2018090905    2062       17          35.0          30.0        40.5   
75230  2018090905    2062       17          35.0          30.0        40.5   
74891  2018090905    2062       17          35.0          30.0        41.5   
...           ...     ...      ...           ...           ...         ...   
76037  2018090905    2062       17          35.0          30.0        82.5   
76038  2018090905    2062       17          35.0          30.0        83.5   
76039  2018090905    2062       17          35.0          30.0        84.5   
76040  2018090905    2062       17          35.0          30.0        85.5   
78029  2018090905    2062       17          35.0          30.0       119.5   

       ball_end_y    cp_off  
76676        38.5  0.052401  
74976        18.5  0.051102  
75145        20.5  0.049128  
75230        21.5  0.044516  
74891        17.5  0.042800  
...           ...       ...  
76037        30.5  0.000000  
76038        30.5  0.000000  
76039        30.5  0.000000  
76040        30.5  0.000000  
78029        53.3  0.000000  

[4590 rows x 8 columns]

In [15]:
from visualize import AnimatePlay
animated_play = AnimatePlay(play_df, 20, field_dfs)
HTML(animated_play.ani.to_jshtml())

ValueError: 'vertices' must be 2D with shape (M, 2). Your input has shape (0,).

In [58]:
# Utility Libraries
from datetime import datetime
import matplotlib as mpl
import pytz
import pandas as pd

# Computation Libraries
import numpy as np

# Plotting libraries
import matplotlib.pyplot as plt
from matplotlib import animation
import matplotlib.patches as patches

from matplotlib.path import Path

verts = [
    (-0.4, 0.),  # left, bottom
    (-0.2, 0.2),  # left, top
    (0.2, 0.2),  # right, top
    (0.4, -0.),  # right, bottom
    (0.2, -0.2),  # left, bottom
    (-0.2, -0.2),  # left, top
    (-0.4, 0),  # left, bottom
]

codes = [
    Path.MOVETO,
    Path.LINETO,
    Path.LINETO,
    Path.LINETO,
    Path.LINETO,
    Path.LINETO,
    Path.CLOSEPOLY,
]

ballPath = Path(verts, codes, closed=True)


colors = pd.read_csv(
    'https://raw.githubusercontent.com/uditrana/NFLFastR_analysis/master/nfl_colors.tsv', delimiter='\t')

class AnimatePlay:
    def __init__(self, play_df, plot_size_len, pitch_control_df=None) -> None:
        """Initializes the datasets used to animate the play.

        Parameters
        ----------
        play_df : DataFrame
            Dataframe corresponding to the play information for the play that requires
            animation. This data will come from the weeks dataframe and contains position
            and velocity information for each of the players and the football.

        Returns
        -------
        None
        """
        self._MAX_FIELD_Y = 53.3
        self._MAX_FIELD_X = 120
        self._MAX_FIELD_PLAYERS = 22

        self._show_control = type(pitch_control_df) != type(None)
        self._pitch_control_df = pitch_control_df
        # self._CPLT = sns.color_palette("husl", 2)
        self._offense_color = colors.loc[colors.team == play_df.loc[play_df.team_pos == 'OFF']['teamAbbr'].iloc[0]]
        self._defense_color = colors.loc[colors.team == play_df.loc[play_df.team_pos == 'DEF']['teamAbbr'].iloc[0]]
        self._frame_data = play_df
        self._game_id, self._play_id = play_df.iloc[:1][['gameId', 'playId']].to_records(index=False)[0]
        self._times = sorted(play_df.time.unique())
        self._stream = self.data_stream()

        self._date_format = "%Y-%m-%dT%H:%M:%S.%fZ"
        self._mean_interval_ms = np.mean(
            [delta.microseconds / 1000
             for delta in np.diff(
                 np.array(
                     [pytz.timezone('US/Eastern').localize(datetime.strptime(date_string, self._date_format))
                      for date_string in self._times]))])

        self._fig = plt.figure(figsize=(plot_size_len, plot_size_len*(self._MAX_FIELD_Y/self._MAX_FIELD_X)))

        self._ax_field = plt.gca()

        self._ax_offense = self._ax_field.twinx()
        self._ax_defense = self._ax_field.twinx()
        self._ax_jersey = self._ax_field.twinx()

        self.ani = animation.FuncAnimation(
            self._fig, self.update, frames=len(self._times),
            interval=self._mean_interval_ms, init_func=self.setup_plot, blit=False)

        plt.close()

    @staticmethod
    def set_axis_plots(ax, max_x, max_y) -> None:
        ax.xaxis.set_visible(False)
        ax.yaxis.set_visible(False)

        ax.set_xlim([0, max_x])
        ax.set_ylim([0, max_y])

    @staticmethod
    def convert_orientation(x):
        return (-x + 90) % 360

    @staticmethod
    def polar_to_z(r, theta):
        return r * np.exp(1j * theta)

    @staticmethod
    def deg_to_rad(deg):
        return deg*np.pi/180

    def data_stream(self):
        for time in self._times:
            yield self._frame_data[self._frame_data.time == time]

    def setup_plot(self):
        self.set_axis_plots(self._ax_field, self._MAX_FIELD_X, self._MAX_FIELD_Y)

        # ball_snap_df = self._frame_data[(self._frame_data.event == 'ball_snap') & (self._frame_data.team == 'football')]
        self._ax_field.axvline(self._frame_data.iloc[0]['los'], color='k', linestyle='--')
        self._ax_field.set_title(f"game {self._game_id} play {self._play_id}", c='white')
        self._frame_text = self._ax_field.text(5, 51, 0, fontsize=15, color='white', ha='center')
        self._event_text = self._ax_field.text(5, 49, None, fontsize=10, color='white', ha='center')

        self.set_axis_plots(self._ax_offense, self._MAX_FIELD_X, self._MAX_FIELD_Y)
        self.set_axis_plots(self._ax_defense, self._MAX_FIELD_X, self._MAX_FIELD_Y)
        self.set_axis_plots(self._ax_jersey, self._MAX_FIELD_X, self._MAX_FIELD_Y)

        for idx in range(10, 120, 10):
            self._ax_field.axvline(idx, color='k', linestyle='-', alpha=0.05)

        self._ax_field.add_patch(patches.Rectangle((0, 0), 10, self._MAX_FIELD_Y,
                                                   color=self._defense_color['color1'].to_string(index=False).strip()))
        self._ax_field.add_patch(patches.Rectangle((110, 0), 10, self._MAX_FIELD_Y,
                                                   color=self._offense_color['color1'].to_string(index=False).strip()))

        if self._show_control:
            self._scat_control = self._ax_field.scatter(
                [],
                [],
                s=80, marker='s', alpha=0.9,
                norm=mpl.colors.Normalize(vmin=-1., vmax=1.), cmap='RdBu')

        self._scat_offense = self._ax_offense.scatter(
            [],
            [],
            s=500, color=self._offense_color['color1'],
            edgecolors=self._offense_color['color2'])
        self._scat_defense = self._ax_defense.scatter(
            [],
            [],
            s=500, color=self._defense_color['color1'],
            edgecolors=self._defense_color['color2'])

        self._scat_jersey_list = []
        self._scat_number_list = []
        self._scat_name_list = []
        self._vel_list = []
        self._acc_list = []
        for _ in range(self._MAX_FIELD_PLAYERS):
            self._scat_jersey_list.append(self._ax_jersey.text(
                0, 0, '', horizontalalignment='center', verticalalignment='center', c='white'))
            self._scat_number_list.append(self._ax_jersey.text(
                0, 0, '', horizontalalignment='center', verticalalignment='center', c='black'))
            self._scat_name_list.append(self._ax_jersey.text(
                0, 0, '', horizontalalignment='center', verticalalignment='center', c='black'))

            self._vel_list.append(self._ax_field.add_patch(patches.Arrow(0, 0, 0, 0, color='k')))
            self._acc_list.append(self._ax_field.add_patch(patches.Arrow(0, 0, 0, 0, color='k')))
        
        self._scat_field = self._ax_field.scatter([], [], s=200, color=colors.loc[colors.team == 'FTBL']['color1'], marker=ballPath)

        return (self._scat_field, self._scat_offense, self._scat_defense, *self._scat_jersey_list, *self._scat_number_list, *self._scat_name_list)

    def update(self, anim_frame):
        pos_df = next(self._stream)
        frameId = pos_df.frameId.unique()[0]
        event = pos_df.event.unique()[0]
        self._frame_text.set_text(str(frameId))
        self._event_text.set_text(str(event))

        for label in pos_df.team_pos.unique():
            label_data = pos_df[pos_df.team_pos == label]

            if label == 'FTBL':
                self._scat_field.set_offsets(np.hstack([label_data.x, label_data.y]))
            elif label == 'OFF':
                self._scat_offense.set_offsets(np.vstack([label_data.x, label_data.y]).T)
            elif label == 'DEF':
                self._scat_defense.set_offsets(np.vstack([label_data.x, label_data.y]).T)

        # jersey_df = pos_df[pos_df.jerseyNumber.notnull()]

        if self._show_control:
            pc = self._pitch_control_df.at[frameId, 'pc']
            if hasattr(pc, '__iter__'):
                self._scat_control.set_offsets(np.array(list(map(lambda x: [x[0][0], x[0][1]], pc))))
                self._scat_control.set_array(np.array(list(map(lambda x: x[1], pc))))
                self._scat_control.set_cmap('RdBu')
            else:
                self._scat_control.set_offsets([])
                

        for (index, row) in pos_df[pos_df.jerseyNumber.notnull()].reset_index().iterrows():
            self._scat_jersey_list[index].set_position((row.x, row.y))
            self._scat_jersey_list[index].set_text(row.position)
            self._scat_number_list[index].set_position((row.x, row.y+1.9))
            self._scat_number_list[index].set_text(int(row.jerseyNumber))
            self._scat_name_list[index].set_position((row.x, row.y-1.9))
            self._scat_name_list[index].set_text(row.displayName.split()[-1])

            # player_orientation_rad = self.deg_to_rad(self.convert_orientation(row.o))
            # player_direction_rad = row.dir_rad
            # player_speed = row.s
            # player_accel = row.a

            # player_vel = np.array([np.real(self.polar_to_z(player_speed, player_direction_rad)),
            #                        np.imag(self.polar_to_z(player_speed, player_direction_rad))])
            # player_orient = np.array([np.real(self.polar_to_z(2, player_orientation_rad)),
            #                           np.imag(self.polar_to_z(2, player_orientation_rad))])

            self._vel_list[index].remove()
            self._vel_list[index] = self._ax_field.add_patch(
                patches.Arrow(row.x, row.y, row.v_x, row.v_y, color='k'))

            self._acc_list[index].remove()
            self._acc_list[index] = self._ax_field.add_patch(
                patches.Arrow(row.x, row.y, row.a_x, row.a_y, color='grey', width=2))

        return (self._scat_field, self._scat_offense, self._scat_defense, *self._scat_jersey_list, *self._scat_number_list, *self._scat_name_list)

In [62]:
pc_df.at[1, 'pc']

),
 ((56.5, 51.5), 0.0),
 ((57.5, 51.5), 0.0),
 ((58.5, 51.5), 0.0),
 ((59.5, 51.5), 0.0),
 ((60.5, 51.5), 0.0),
 ((61.5, 51.5), 0.0),
 ((62.5, 51.5), 0.0),
 ((63.5, 51.5), 0.0),
 ((64.5, 51.5), 0.0),
 ((65.5, 51.5), 0.0),
 ((66.5, 51.5), 0.0),
 ((67.5, 51.5), 0.0),
 ((68.5, 51.5), 0.0),
 ((69.5, 51.5), 0.0),
 ((70.5, 51.5), 0.0),
 ((71.5, 51.5), 0.0),
 ((72.5, 51.5), 0.0),
 ((73.5, 51.5), 0.0),
 ((74.5, 51.5), 0.0),
 ((75.5, 51.5), 0.0),
 ((76.5, 51.5), 0.0),
 ((77.5, 51.5), 0.0),
 ((78.5, 51.5), 0.0),
 ((79.5, 51.5), 0.0),
 ((80.5, 51.5), 0.0),
 ((81.5, 51.5), 0.0),
 ((82.5, 51.5), 0.0),
 ((83.5, 51.5), 0.0),
 ((84.5, 51.5), 0.0),
 ((85.5, 51.5), 0.0),
 ((86.5, 51.5), 0.0),
 ((87.5, 51.5), 0.0),
 ((88.5, 51.5), 0.0),
 ((89.5, 51.5), 0.0),
 ((90.5, 51.5), 0.0),
 ((91.5, 51.5), 0.0),
 ((92.5, 51.5), 0.0),
 ((93.5, 51.5), 0.0),
 ((94.5, 51.5), 0.0),
 ((95.5, 51.5), 0.0),
 ((96.5, 51.5), 0.0),
 ((97.5, 51.5), 0.0),
 ((98.5, 51.5), 0.0),
 ((99.5, 51.5), 0.0),
 ((100.5, 51.5), 0.0),
 ((101

In [59]:
animated_play = AnimatePlay(play_df, 20, pc_df)
HTML(animated_play.ani.to_jshtml())

In [48]:
pc = pd.DataFrame(pc_df.at[39, 'pc'], columns=['x', 'y', 'p'])
pc.loc[(pc.x>50)&(pc.y<10)].sort_values('p')

x    y     p
4528  58.5  2.5 -0.52
4618  58.5  1.5 -0.26
4707  57.5  0.5 -0.25
4617  57.5  1.5 -0.16
4708  58.5  0.5 -0.14
...    ...  ...   ...
3891  51.5  9.5  0.26
3983  53.5  8.5  0.27
3984  54.5  8.5  0.29
3892  52.5  9.5  0.29
3893  53.5  9.5  0.31

[700 rows x 3 columns]

In [ ]:
# USELESS JUNK BELOW

In [ ]:
# Select the game and play that you wish to see in week 1
import random

plays = list(track_df.groupby(['gameId', 'playId'], as_index=False).first()[['gameId', 'playId']].to_records(index=False))

game_id = 2018122314
play_id = 4239

# game_id, play_id = random.choice(plays)

play_df = track_df[(track_df.playId == play_id) & (track_df.gameId == game_id)].sort_values(by = 'time')
play_df.head()

In [ ]:
frame = 40
frame_df = play_df[(play_df.nflId!=0)&(play_df.frameId == 40)][['nflId', 'displayName', 'position', 'team_pos', 'x', 'y', 'v_x', 'v_y', 'v_mag', 'v_theta', 'a_x', 'a_y', 'a_mag', 'a_theta']]

In [ ]:
frame_df.head()

In [ ]:
a_max = 8
v_max = 9
reax_t = v_max/a_max

frame_df['v_x_r'] = frame_df.a_x*reax_t+frame_df.v_x
frame_df['v_y_r'] = frame_df.a_y*reax_t+frame_df.v_y
frame_df['v_r_mag'] = np.linalg.norm(np.array([frame_df.v_x_r, frame_df.v_y_r]), axis=0)
frame_df['v_r_theta'] = np.arctan(frame_df.v_y_r/frame_df.v_x_r).fillna(0)

frame_df['x_r'] = frame_df.x + frame_df.v_x*reax_t - 0.5*frame_df.a_x*reax_t**2
frame_df['y_r'] = frame_df.y + frame_df.v_y*reax_t - 0.5*frame_df.a_y*reax_t**2
frame_df

In [ ]:
frame_df['T_b'] = 2.7
frame_df['x_b'] = 75
frame_df['y_b'] = 20

frame_df['int_d_x'] = frame_df.x_b-frame_df.x_r
frame_df['int_d_y'] = frame_df.y_b-frame_df.y_r
frame_df['int_d_mag'] = np.linalg.norm(np.array([frame_df.int_d_x, frame_df.int_d_y]), axis=0)
frame_df['int_d_theta'] = np.arctan(frame_df.int_d_y/frame_df.int_d_x).fillna(0)

frame_df

In [ ]:
frame_df['int_v0'] = (frame_df['v_x_r']*frame_df['int_d_x'] + frame_df['v_y_r']*frame_df['int_d_y'])/frame_df['int_d_mag']

frame_df['d_lt_vm'] = (v_max**2-frame_df.int_v0**2)/(2*a_max)
frame_df['t_lt_vm'] = (v_max-frame_df.int_v0)/(a_max)
frame_df['d_at_vm'] = frame_df.int_d_mag-frame_df.d_lt_vm
frame_df['t_at_vm'] = frame_df.d_at_vm/v_max
frame_df['t_tot'] = frame_df.t_lt_vm+frame_df.t_at_vm
frame_df['int_dT'] = frame_df.T_b - frame_df.t_tot

frame_df.sort_values('t_tot', ascending=True)


In [ ]:
tti_sigma = 0.45
frame_df['P_int_T_j'] = (1/(1. + np.exp( -np.pi/np.sqrt(3.0)/tti_sigma * (frame_df.int_dT) ) )).round(2) 

frame_df[['displayName', 'team_pos', 'P_int_T_j']].sort_values('P_int_T_j', ascending=False)

In [ ]:
animated_play = AnimatePlay(play_df, 20)
HTML(animated_play.ani.to_jshtml())

In [ ]:


frame = 40
frame_df = play_df[(play_df.nflId!=0)&(play_df.frameId == 40)][['nflId', 'displayName', 'position', 'team_pos', 'x', 'y', 'v_x', 'v_y', 'v_mag', 'v_theta', 'a_x', 'a_y', 'a_mag', 'a_theta']]

frame_df = frame_df.copy()
frame_df = frame_df[['nflId', 'displayName', 'position', 'team_pos', 'x', 'y', 'v_x', 'v_y', 'v_mag', 'v_theta', 'a_x', 'a_y', 'a_mag', 'a_theta']]

start_loc = frame_df.loc[frame_df.position=='QB'][['x', 'y']].iloc[0]
frame_df = frame_df.loc[frame_df.position!='QB']

target_locs = np.array([np.array([x, y]) for y in range(52, -1, -1) for x in range(int(start_loc[0]), 120) ])
target_locs = target_locs + 0.5

start_locs = np.full_like(target_locs, start_loc)
tofs = np.linalg.norm(start_locs - target_locs, axis=1)/params.avg_ball_speed

frame_df['v_x_r'] = frame_df.a_x*reax_t+frame_df.v_x
frame_df['v_y_r'] = frame_df.a_y*reax_t+frame_df.v_y
frame_df['v_r_mag'] = np.linalg.norm(np.array([frame_df.v_x_r, frame_df.v_y_r]), axis=0)
frame_df['v_r_theta'] = np.arctan(frame_df.v_y_r/frame_df.v_x_r).fillna(0)

frame_df['x_r'] = frame_df.x + frame_df.v_x*reax_t - 0.5*frame_df.a_x*reax_t**2
frame_df['y_r'] = frame_df.y + frame_df.v_y*reax_t - 0.5*frame_df.a_y*reax_t**2

frame_df

In [ ]:
PCS = dict()

for i, (ball_x, ball_y) in enumerate(target_locs):
    # i, (ball_x, ball_y) = random.choice(list(enumerate(target_locs)))
    # print(i, ball_x, ball_y, tofs[i])

    df = frame_df.copy()
    df['int_d_x'] = ball_x-df.x_r
    df['int_d_y'] = ball_y-df.y_r
    df['int_d_mag'] = np.linalg.norm(np.array([df.int_d_x, df.int_d_y]), axis=0)
    df['int_d_theta'] = np.arctan(df.int_d_y/df.int_d_x).fillna(0)

    df['int_v0'] = (df['v_x_r']*df['int_d_x'] + df['v_y_r']*df['int_d_y'])/df['int_d_mag']

    df['d_lt_vm'] = (params.v_max**2-df.int_v0**2)/(2*params.a_max)
    df['t_lt_vm'] = (params.v_max-df.int_v0)/(params.a_max)
    df['d_at_vm'] = df.int_d_mag-df.d_lt_vm
    df['t_at_vm'] = df.d_at_vm/v_max
    df['t_tot'] = df.t_lt_vm+df.t_at_vm
    df['int_dT'] = tofs[i] - df.t_tot
    df['P_int_T_j'] = (1/(1. + np.exp( -np.pi/np.sqrt(3.0)/params.tti_sigma * (df.int_dT) ) )).round(2)

    topOff = df.loc[df.team_pos=="OFF"].sort_values('P_int_T_j', ascending=False)['P_int_T_j'].iloc[0]
    topDef = df.loc[df.team_pos=="DEF"].sort_values('P_int_T_j', ascending=False)['P_int_T_j'].iloc[0]

    # topOff-topDef
    PCS[(ball_x, ball_y)] = round(topOff-topDef, 2)

